In [1]:
import math
import collections

import pandas as pd
import numpy as np
from keras import Input,backend
from keras.models import Model, Sequential
from keras.layers import *
from keras.callbacks import Callback
from sklearn.metrics import confusion_matrix, f1_score, precision_score, recall_score, accuracy_score, matthews_corrcoef

Using TensorFlow backend.


In [2]:
dataset = pd.read_csv("../datasets/train_test_data.csv",
                           header=0, parse_dates=[0], index_col=0)

#params for generator
label_index = len(dataset.columns) -1


In [99]:
#hyperparamters
batch_size=64

#params for generator
delay=10
step=1 # 1 timestep = 1 day
lookback=10

#ratio for train/val/test split
train_ratio=0.7
val_ratio=0.15

train_max_idx = math.ceil(len(dataset)*train_ratio)
val_max_idx = math.ceil(len(dataset)*(train_ratio+val_ratio))

# 1 step = 1 batche of samples 
train_steps = (train_max_idx+1) // batch_size
val_steps =  (val_max_idx - train_max_idx - lookback) // batch_size
test_steps = (len(dataset) - val_max_idx - lookback) // batch_size

In [100]:
def generator_for_binary_classifier(data, label_index, lookback, delay, min_index, max_index,
              shuffle=False, batch_size=64, step=1, interval_label=False):
    if max_index is None:
        max_index = len(data) - delay - 1
    i = min_index + lookback
    while 1:
        if shuffle:
            rows = np.random.randint(
                min_index + lookback, max_index, size=batch_size)
        else:
            if i + batch_size >= max_index: 
                i = min_index + lookback #reset 'i'
            rows = np.arange(i, min(i + batch_size, max_index))
            i += len(rows)

        samples = np.zeros((len(rows),
                           lookback // step,
                           (data.shape[-1])))
        labels = np.zeros((len(rows),))
        
        #generate one batch of samples and targets
        for j, row in enumerate(rows):
            indices = range(rows[j] - lookback, rows[j], step)
            samples[j] = data[indices]
            
            if interval_label is False:
                labels[j] = data[rows[j] + delay][label_index]
            else:
                labels[j] = 1 if 1 in data[rows[j]:(rows[j] + delay)][:,label_index] else 0
                
        yield samples, labels

In [101]:
#init generator_for_binary_classifiers
train_rand_gen = generator_for_binary_classifier(dataset.to_numpy(),
                      label_index=label_index,
                      lookback=lookback,
                      delay=delay,
                      min_index=0,
                      max_index=train_max_idx,
                      shuffle=True,
                      step=step, 
                      batch_size=batch_size,
                      interval_label=True)
train_gen = generator_for_binary_classifier(dataset.to_numpy(),
                      label_index=label_index,
                      lookback=lookback,
                      delay=delay,
                      min_index=0,
                      max_index=train_max_idx,
                      shuffle=False,
                      step=step, 
                      batch_size=batch_size,
                      interval_label=True)



val_gen = generator_for_binary_classifier(dataset.to_numpy(),
                    label_index=label_index,
                      lookback=lookback,
                      delay=delay,
                      min_index=train_max_idx+1,
                      max_index=val_max_idx,
                      shuffle=False,
                      step=step, 
                      batch_size=batch_size,
                      interval_label=True)

test_gen = generator_for_binary_classifier(dataset.to_numpy(),
                      label_index=label_index,
                      lookback=lookback,
                      delay=delay,
                      min_index=val_max_idx+1,
                      max_index=None,
                      shuffle=False,
                      step=step, 
                      batch_size=batch_size,
                      interval_label=True)


In [102]:
X,Y=generator_to_samples_and_targets(train_rand_gen, train_steps)

print(X.shape)
print(Y.shape)
print(collections.Counter(Y))

IM here
row = 1672, row + delay=1682
[[0.36344155 0.76376348 0.37913939 0.43582964 0.61883276 0.59931933
  0.43292555 0.61537882 0.50760735 0.50070873 0.57485541 0.49287255
  0.49103385 0.53085565 0.30814734 0.61060973 0.52306413 0.47961165
  0.43650761 0.80162602 0.64424998 0.17189378 0.09909055 0.        ]
 [0.49846771 0.38956216 0.42080776 0.49291701 0.66469573 0.43592373
  0.48490445 0.63536873 0.50760735 0.61299371 0.56539537 0.48026222
  0.49140035 0.4702363  0.30814734 0.61060973 0.52306413 0.47961165
  0.43650761 0.80162602 0.64424998 0.17189378 0.09909055 0.        ]
 [0.55814095 0.50546727 0.4231342  0.44758273 0.59997641 0.54729107
  0.46125571 0.61092158 0.50760735 0.62463792 0.50284342 0.42558106
  0.49213334 0.47358206 0.30814734 0.61060973 0.52306413 0.47961165
  0.43650761 0.80162602 0.64424998 0.17189378 0.09909055 0.        ]
 [0.49144873 0.33788493 0.42623026 0.41692728 0.51546706 0.40652482
  0.47496894 0.56360643 0.42079597 0.56641934 0.54260236 0.54136047
  0.4921

IM here
row = 1997, row + delay=2007
[[0.4282599  0.41612834 0.46468578 0.42686638 0.42669139 0.44929294
  0.47647276 0.56103533 0.4080367  0.62657649 0.52053859 0.50864146
  0.49323293 0.47048538 0.55551945 0.61277498 0.75327619 0.43321963
  0.42071412 0.58861789 0.62224887 0.6454235  0.24128848 0.        ]
 [0.48549885 0.32227833 0.43939128 0.42387103 0.41687391 0.37135559
  0.4636815  0.56343427 0.43312711 0.50576051 0.57384008 0.61977254
  0.48003931 0.51320891 0.55551945 0.61277498 0.75327619 0.43321963
  0.42071412 0.58861789 0.62224887 0.6454235  0.24128848 0.        ]
 [0.41527354 0.3347063  0.35225781 0.38087794 0.30210584 0.40144986
  0.45027273 0.48181455 0.36727222 0.46413082 0.63270182 0.52219922
  0.50129937 0.4566952  0.55551945 0.61277498 0.75327619 0.43321963
  0.42071412 0.58861789 0.62224887 0.6454235  0.24128848 0.        ]
 [0.5530718  0.38081028 0.35420901 0.40520861 0.16665188 0.40957335
  0.45074005 0.56703941 0.36727222 0.50582986 0.5773912  0.52435859
  0.4935

  0.44807267 0.59481595 0.59542995 0.1058515  0.3017     0.        ]]
IM here
row = 576, row + delay=586
[[0.46833033 0.30249897 0.32470982 0.29685766 0.20184959 0.5179885
  0.45317885 0.46786484 0.45420344 0.50993627 0.44548393 0.54621499
  0.49767314 0.48082533 0.38965578 0.54805195 0.71776744 0.56796117
  0.93292908 0.56753956 0.70252639 0.47202418 0.31178869 1.        ]
 [0.46833033 0.34948827 0.32976051 0.29685766 0.71062433 0.3703427
  0.46283115 0.52188426 0.36476674 0.47406992 0.45262742 0.52147522
  0.47665206 0.46257851 0.38965578 0.54805195 0.71776744 0.56796117
  0.93292908 0.56753956 0.70252639 0.47202418 0.31178869 0.        ]
 [0.43042224 0.65148109 0.42170522 0.49447566 0.40161018 0.41879117
  0.57045989 0.4998567  0.46852795 0.58093809 0.48340517 0.55885605
  0.49398544 0.4799385  0.38965578 0.54805195 0.71776744 0.56796117
  0.93292908 0.56753956 0.70252639 0.47202418 0.31178869 0.        ]
 [0.4861301  0.27055368 0.5333236  0.49447566 0.65754689 0.36974034
  0.459854

[[0.55257199 0.30643667 0.31344646 0.36788954 0.37339211 0.40545498
  0.39190726 0.52690171 0.43669865 0.41124671 0.55910229 0.52079241
  0.50576976 0.4441798  0.35270614 0.59563164 0.64174609 0.33656958
  0.43075237 0.57257029 0.6891252  0.18791897 0.26589965 0.        ]
 [0.46563419 0.42628856 0.25186574 0.47108854 0.27424023 0.49254721
  0.53894223 0.5690563  0.43991822 0.58692524 0.57112591 0.54486092
  0.49618876 0.49654228 0.35270614 0.59563164 0.64174609 0.33656958
  0.43075237 0.57257029 0.6891252  0.18791897 0.26589965 1.        ]
 [0.52201774 0.41169982 0.54440398 0.43659612 0.61548385 0.44738382
  0.44219333 0.58242688 0.4725778  0.52760665 0.54671521 0.51728889
  0.49397898 0.47925749 0.35270614 0.59563164 0.64174609 0.33656958
  0.43075237 0.57257029 0.6891252  0.18791897 0.26589965 0.        ]
 [0.49713497 0.24524086 0.42714578 0.41595226 0.37307129 0.35169285
  0.45858602 0.56769481 0.51086366 0.52760665 0.5478298  0.46706523
  0.49250626 0.47074487 0.35270614 0.59563164

  0.4527068  0.60073604 0.63344559 0.21970683 0.28263492 0.        ]]
IM here
row = 3240, row + delay=3250
[[0.52060373 0.48412212 0.48035177 0.53717959 1.         0.43366311
  0.53506327 0.72369652 0.60040795 0.61558208 0.37855447 0.50135084
  0.49103385 0.4968213  0.42100143 0.60195279 0.82456675 0.47043248
  0.42740461 0.57415421 0.76342517 0.25466431 0.34421708 0.        ]
 [0.66949796 0.55577439 0.46568222 0.59160304 0.91768943 0.60256039
  0.52324962 0.76734887 0.62429101 0.66284342 0.49688248 0.44889878
  0.44205841 0.45191327 0.37820644 0.59847738 0.83933454 0.79935275
  0.40511798 0.66789563 0.69069665 0.25796291 0.33039542 0.        ]
 [0.51606163 0.36317177 0.50474418 0.43045625 0.55595049 0.41987869
  0.48002255 0.59638782 0.62429101 0.67665687 0.57013887 0.51879606
  0.4950914  0.51470387 0.37820644 0.59847738 0.83933454 0.79935275
  0.40511798 0.66789563 0.69069665 0.25796291 0.33039542 0.        ]
 [0.55099285 0.44129814 0.42507992 0.4969366  0.71575424 0.52269723
  0.51

...

IM here
row = 3953, row + delay=3963
[[0.46444245 0.45327839 0.39855084 0.42782029 0.49430337 0.46721759
  0.4863332  0.55348471 0.47464373 0.57483359 0.5549893  0.57523913
  0.49840066 0.50386868 0.37080186 0.59902597 0.48862975 0.37864078
  0.3989661  0.52217295 0.6024331  0.22160695 0.21688797 0.        ]
 [0.56737753 0.41709932 0.48733064 0.41610018 0.43646679 0.44370168
  0.4697824  0.56375726 0.44884815 0.61042881 0.57555983 0.4699923
  0.49250683 0.47487842 0.37080186 0.59902597 0.48862975 0.37864078
  0.3989661  0.52217295 0.6024331  0.22160695 0.21688797 0.        ]
 [0.51282237 0.40209331 0.39899466 0.39203404 0.48744723 0.45754817
  0.48424996 0.59339988 0.45101363 0.55232578 0.55088467 0.47032851
  0.49250676 0.46436767 0.37080186 0.59902597 0.48862975 0.37864078
  0.3989661  0.52217295 0.6024331  0.22160695 0.21688797 0.        ]
 [0.43140321 0.33633661 0.39511116 0.38817165 0.43167095 0.42371668
  0.48683887 0.54260517 0.4249041  0.57473747 0.5549907  0.51733754
  0.49177

IM here
row = 3251, row + delay=3261
[[0.51575969 0.53054484 0.3687106  0.46376023 0.59951255 0.58568465
  0.47624739 0.49858201 0.35073153 0.59644643 0.5886317  0.38143198
  0.51797306 0.47542813 0.37820644 0.59847738 0.83933454 0.79935275
  0.40511798 0.66789563 0.69069665 0.25796291 0.33039542 0.        ]
 [0.54695399 0.52001992 0.4557352  0.51536061 0.58574578 0.42984657
  0.50654511 0.7141216  0.55523459 0.6645108  0.51491576 0.44952972
  0.48660965 0.4710564  0.37820644 0.59847738 0.83933454 0.79935275
  0.40511798 0.66789563 0.69069665 0.25796291 0.33039542 0.        ]
 [0.45362131 0.49056606 0.44640088 0.40928829 0.55141132 0.41337985
  0.52304042 0.58235311 0.46920739 0.58556663 0.54801527 0.51148498
  0.49177133 0.45527534 0.37820644 0.59847738 0.83933454 0.79935275
  0.40511798 0.66789563 0.69069665 0.25796291 0.33039542 0.        ]
 [0.42355594 0.2643986  0.41134476 0.37262878 0.51452442 0.35698357
  0.4659074  0.55961297 0.41261332 0.46868579 0.48142213 0.49149374
  0.4939

  0.40041057 0.46573751 0.62123989 0.1401702  0.27791095 0.        ]]
IM here
row = 2178, row + delay=2188
[[0.49920683 0.34891455 0.36542221 0.43400852 0.37721621 0.45758481
  0.48761603 0.56384276 0.41695315 0.56682652 0.42859941 0.48551536
  0.47563478 0.45438073 0.32462313 0.59369202 0.570558   0.37864078
  0.45413682 0.53736854 0.69248498 0.24228872 0.30213321 0.        ]
 [0.49892393 0.41497253 0.49332152 0.42305369 0.46577902 0.39640839
  0.48296065 0.56860337 0.41379288 0.54608164 0.5705738  0.52255951
  0.49250122 0.50037506 0.32462313 0.59369202 0.570558   0.37864078
  0.45413682 0.53736854 0.69248498 0.24228872 0.30213321 0.        ]
 [0.45833451 0.43209453 0.43093051 0.40345848 0.54292791 0.46739882
  0.47064566 0.55669953 0.47394526 0.59670336 0.61831572 0.56613699
  0.49543573 0.51750532 0.32462313 0.59369202 0.570558   0.37864078
  0.45413682 0.53736854 0.69248498 0.24228872 0.30213321 0.        ]
 [0.38372788 0.42610717 0.4705423  0.45015337 0.56817184 0.48520239
  0.48

  0.41615005 0.57966243 1.         0.25021501 0.21990221 0.        ]]
IM here
row = 136, row + delay=146
[[0.54760948 0.41669688 0.40279104 0.41739398 0.56368981 0.42449995
  0.50439322 0.58523062 0.4795826  0.64055033 0.55645611 0.48255686
  0.49509481 0.49253181 0.35000294 1.         0.64926675 0.15064203
  0.38785341 0.59002354 0.59376082 0.42410658 0.25891914 0.        ]
 [0.57627416 0.34529945 0.40072576 0.39035972 0.50525824 0.39594173
  0.48001713 0.52827685 0.42811013 0.55416872 0.56880707 0.4942558
  0.4932486  0.48307482 0.35000294 1.         0.64926675 0.15064203
  0.38785341 0.59002354 0.59376082 0.42410658 0.25891914 0.        ]
 [0.46149054 0.38354996 0.40166629 0.37389886 0.50944701 0.3496097
  0.48118282 0.56216877 0.38541662 0.53395597 0.55425378 0.53522005
  0.48069913 0.49897465 0.35000294 1.         0.64926675 0.15064203
  0.38785341 0.59002354 0.59376082 0.42410658 0.25891914 0.        ]
 [0.53995437 0.45992984 0.38411106 0.37825244 0.50432758 0.46045039
  0.468032

KeyboardInterrupt: 

In [6]:
def print_metric(y_true, Y_pred):
    print('F1 score: %f' % f1_score(y_true, Y_pred))
    print('precision score: %f' % precision_score(y_true, Y_pred))
    print('recall score: %f' % recall_score(y_true, Y_pred))
    print('accuracy score: %f' % accuracy_score(y_true, Y_pred))
    print('matthews_corrcoef: %f' % matthews_corrcoef(y_true, Y_pred))
    print('\nConfusion matrix:')
    print(confusion_matrix(y_true, Y_pred, labels=[0,1]))

In [7]:
def probs_to_binary_classes(preds, threshold=0.5):
    """
    preds: np array
    threshold: scalar
    """
    return np.where(preds > threshold, 1, 0)

In [8]:
def print_unique_counts(x):
    unique, counts = np.unique(x, return_counts=True)
    print(np.asarray((unique, counts)).T)


In [9]:
#build s FC model from the book

input_shape = (lookback//step, dataset.shape[-1] - 1)

model = Sequential()
model.add(Flatten(input_shape=input_shape))
model.add(Dense(32, activation='relu'))
model.add(Dense(1, activation='sigmoid'))

model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
print(model.summary())

# #fit the model
model.fit_generator(train_rand_gen,
                    steps_per_epoch=train_steps,
                    epochs=50, verbose=1)

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
flatten_1 (Flatten)          (None, 250)               0         
_________________________________________________________________
dense_1 (Dense)              (None, 32)                8032      
_________________________________________________________________
dense_2 (Dense)              (None, 1)                 33        
Total params: 8,065
Trainable params: 8,065
Non-trainable params: 0
_________________________________________________________________
None
Epoch 1/50
61/61 [==============================] - 0s 8ms/step - loss: 0.5478 - acc: 0.7551
Epoch 2/50
61/61 [==============================] - 0s 6ms/step - loss: 0.5308 - acc: 0.7531
Epoch 3/50
61/61 [==============================] - 0s 6ms/step - loss: 0.5227 - acc: 0.7485
Epoch 4/50
61/61 [==============================] - 0s 5ms/step - loss: 0.5201 - acc: 0.7602
Epoch 5/50
61/61 [=========

In [11]:
def generator_to_samples_and_targets(generator, steps):
    count=0
    X, Y = [], []
    for samples, targets in generator:
        if count >= steps:
            break;
        else:
            count+=1

        X.append(samples)
        Y.append(targets)

    return np.concatenate(X, axis=0), np.concatenate(Y, axis=0)


In [11]:
neg = 2762+158
pos = 177+807
print("We have {0} neg cases and {1} pos cases from train data".format(neg,pos))
print("the common sense baseline (accuracy score) is {0}".format(neg/(pos+neg)))

We have 2920 neg cases and 984 pos cases from train data
the common sense baseline (accuracy score) is 0.7479508196721312


In [12]:
#Make predictions for train set
    
X, Y = generator_to_samples_and_targets(train_gen, train_steps)    
Y_pred = model.predict(X)
print_metric(Y, probs_to_binary_classes(Y_pred))

F1 score: 0.500673
precision score: 0.741036
recall score: 0.378049
accuracy score: 0.809939
matthews_corrcoef: 0.432616

Confusion matrix:
[[2790  130]
 [ 612  372]]


In [13]:
#Make predictions from dev set
X, Y = generator_to_samples_and_targets(val_gen, val_steps)    
Y_pred = model.predict(X)
print_metric(Y, probs_to_binary_classes(Y_pred))


F1 score: 0.000000
precision score: 0.000000
recall score: 0.000000
accuracy score: 0.985577
matthews_corrcoef: -0.004015

Confusion matrix:
[[820   1]
 [ 11   0]]


In [14]:
#Make predictions for test set
X, Y = generator_to_samples_and_targets(test_gen, test_steps)    
Y_pred = model.predict(X)
print_metric(Y, probs_to_binary_classes(Y_pred))


F1 score: 0.000000
precision score: 0.000000
recall score: 0.000000
accuracy score: 0.963942
matthews_corrcoef: 0.000000

Confusion matrix:
[[802   0]
 [ 30   0]]


/home/kevin/anaconda2/envs/py36/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/kevin/anaconda2/envs/py36/lib/python3.6/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/kevin/anaconda2/envs/py36/lib/python3.6/site-packages/sklearn/metrics/classification.py:872: RuntimeWarning: invalid value encountered in double_scalars
  mcc = cov_ytyp / np.sqrt(cov_ytyt * cov_ypyp)
